## **Visualization of pIC<sub>50</sub> values vs. Tanimoto scores.**

The similarity scores computed in KNIME (review article) and the machine learning models calculated in Section 5: Machine Learning Models (GitHub folder) were used to establish a ranking for the three newly generated datasets: INDDS, DIADS, and PYRDS.

In [35]:
import pandas as pd
import matplotlib.pyplot as plt
from scipy.stats import pearsonr
import seaborn as sns

In [18]:
df1 = pd.read_excel("INDDS Library.xlsx")

df2 = pd.read_excel("DIADS Library.xlsx")

df3 = pd.read_excel("PYRDS Library.xlsx")

print(df1.shape)
print(df2.shape)
print(df3.shape)
print(df1.columns)
print(df2.columns)
print(df3.columns)

(78657, 7)
(35222, 7)
(58147, 7)
Index(['NEW_SMILES', 'similarity', 'ppIC$_{50}$ Ridge', 'ppIC$_{50}$ SVR',
       'ppIC$_{50}$ RFR', 'mean', 'std'],
      dtype='object')
Index(['NEW_SMILES', 'similarity', 'ppIC$_{50}$ Ridge', 'ppIC$_{50}$ SVR',
       'ppIC$_{50}$ RFR', 'mean', 'std'],
      dtype='object')
Index(['NEW_SMILES', 'similarity', 'ppIC$_{50}$ SVR', 'ppIC$_{50}$ Ridge',
       'ppIC$_{50}$ RFR', 'mean', 'std'],
      dtype='object')


In [19]:
df1.head(1)

NEW_SMILES  similarity  \
0  O=C(c1ccc(O)cc1)N1CCc2c(n(Cc3ccccc3)c3ccccc23)C1     0.93617   

   ppIC$_{50}$ Ridge  ppIC$_{50}$ SVR  ppIC$_{50}$ RFR      mean       std  
0           6.186882         6.421513         6.166216  6.258204  0.141807

In [20]:
df2.head(1)

NEW_SMILES  similarity  ppIC$_{50}$ Ridge  \
0  CCc1cc(O)c(Oc2ccc(C(N)=O)cc2O)cc1F       0.875           7.497307   

   ppIC$_{50}$ SVR  ppIC$_{50}$ RFR      mean       std  
0         7.232134         7.321892  7.350444  0.134872

In [21]:
df3.head(1)

NEW_SMILES  similarity  ppIC$_{50}$ SVR  \
0  Cc1cc(O)ccc1Oc1cn(C)c(COc2ccccc2)cc1=O      0.8125         6.544182   

   ppIC$_{50}$ Ridge  ppIC$_{50}$ RFR      mean       std  
0           6.720111         6.359792  6.541362  0.180176

### Analysis of QSAR predictions

In [22]:
df1.describe()

similarity  ppIC$_{50}$ Ridge  ppIC$_{50}$ SVR  ppIC$_{50}$ RFR  \
count  78657.000000       78657.000000     78657.000000     78657.000000   
mean       0.455010           5.761603         6.007707         5.932065   
std        0.101284           0.243938         0.248883         0.111694   
min        0.130435           4.780570         5.001199         5.391686   
25%        0.400000           5.597637         5.846237         5.868574   
50%        0.444444           5.762180         6.022895         5.941826   
75%        0.507246           5.923465         6.184933         6.006553   
max        0.936170           6.853364         6.857301         6.363361   

               mean           std  
count  78657.000000  78657.000000  
mean       5.900458      0.176701  
std        0.171987      0.085207  
min        5.141690      0.000715  
25%        5.789728      0.112203  
50%        5.903962      0.170540  
75%        6.015419      0.233301  
max        6.560303      0.558172

In [23]:
df2.describe()

similarity  ppIC$_{50}$ Ridge  ppIC$_{50}$ SVR  ppIC$_{50}$ RFR  \
count  35222.000000       35222.000000     35222.000000     35222.000000   
mean       0.332347           6.283337         6.223171         6.370198   
std        0.117201           0.482718         0.384085         0.438493   
min        0.113924           5.059073         5.295378         5.597699   
25%        0.229730           5.912327         5.934770         6.055657   
50%        0.328125           6.180774         6.160890         6.188325   
75%        0.412698           6.620141         6.471659         6.618854   
max        0.875000           7.798237         7.668725         7.475071   

               mean           std  
count  35222.000000  35222.000000  
mean       6.292236      0.148825  
std        0.418144      0.086339  
min        5.440595      0.000427  
25%        5.973186      0.086015  
50%        6.172865      0.134641  
75%        6.564847      0.193343  
max        7.525855      0.634744

In [24]:
df3.describe()

similarity  ppIC$_{50}$ SVR  ppIC$_{50}$ Ridge  ppIC$_{50}$ RFR  \
count  58147.000000     58147.000000       58147.000000     58147.000000   
mean       0.380204         5.984277           6.217081         6.041148   
std        0.086787         0.268727           0.260313         0.119597   
min        0.180723         5.006073           5.126947         5.523749   
25%        0.315068         5.803450           6.038921         5.974689   
50%        0.358209         5.974135           6.221625         6.042383   
75%        0.424242         6.153956           6.400675         6.112029   
max        0.812500         7.524935           7.122177         6.589035   

               mean           std  
count  58147.000000  58147.000000  
mean       6.080835      0.179969  
std        0.185016      0.090196  
min        5.296944      0.000319  
25%        5.960801      0.111933  
50%        6.078979      0.171478  
75%        6.200318      0.238548  
max        7.047264      0.563928

In [26]:
# Now, define the plot columns
pred_columns = ['ppIC$_{50}$ SVR', 'ppIC$_{50}$ Ridge', 'ppIC$_{50}$ RFR']   #'pIC50_SVR', 'pIC50_RR', 'pIC50_RFR'

# Set up a 3x3 grid for the subplots
fig, axes = plt.subplots(3, 3, figsize=(20, 22), dpi=600)

# Define color schemes for each dataframe
colors = {
    'INDDS': ['royalblue', 'cornflowerblue', 'dodgerblue'],
    'DIADS': ['mediumorchid', 'orchid', 'darkviolet'],
    'PYRDS': ['darkorange', 'orange', 'goldenrod']
}

# Define the dataframes in a dictionary for easier iteration
dataframes = {'INDDS': df1, 'DIADS': df2, 'PYRDS': df3}

# Iterate through each dataframe and prediction column to create the plots
for i, (df_name, df) in enumerate(dataframes.items()):
    for j, pred_col in enumerate(pred_columns):
        # Select color based on the dataframe and prediction column index
        color = colors[df_name][j]
        # Plot the similarity vs current prediction column
        axes[i, j].scatter(df['similarity'], df[pred_col], color=color)
        # Set title, labels, and font size
        axes[i, j].set_xlabel("Tanimoto", fontsize=22)  # Set font size for x-axis label
        axes[i, j].set_ylabel(pred_col, fontsize=22)  # Set font size for y-axis label
        axes[i, j].tick_params(axis='both', labelsize=22)  # Increase font size for axis ticks

# Adjust layout to prevent overlapping labels
plt.tight_layout()
plt.show()

In [32]:
# define the plot columns
pred_columns = ['ppIC$_{50}$ Ridge', 'ppIC$_{50}$ SVR', 'ppIC$_{50}$ RFR']

# Store correlation results
correlation_results = []

# Compute Pearson and Spearman correlations
for df_name, df in dataframes.items():
    for pred_col in pred_columns:
        pearson_corr, _ = pearsonr(df['similarity'], df[pred_col])
        correlation_results.append([df_name, pred_col, pearson_corr])

# Convert to a DataFrame
correlation_df = pd.DataFrame(correlation_results, columns=['Dataset', 'Prediction Model', 'Pearson Correlation'])

correlation_df

Dataset   Prediction Model  Pearson Correlation
0   INDDS  ppIC$_{50}$ Ridge             0.381734
1   INDDS    ppIC$_{50}$ SVR             0.413915
2   INDDS    ppIC$_{50}$ RFR             0.649207
3   DIADS  ppIC$_{50}$ Ridge             0.691691
4   DIADS    ppIC$_{50}$ SVR             0.661635
5   DIADS    ppIC$_{50}$ RFR             0.647115
6   PYRDS  ppIC$_{50}$ Ridge             0.310312
7   PYRDS    ppIC$_{50}$ SVR             0.460617
8   PYRDS    ppIC$_{50}$ RFR             0.593572

In [34]:
# Set up a 2x3 grid for the subplots
fig, axes = plt.subplots(2, 3, figsize=(15, 10), dpi=600)

# Define dataframes and titles with the specified names
dataframes = {
    'INDDB': {'data': df1, 'color_mean': 'royalblue', 'color_std': 'skyblue'},
    'DIADB': {'data': df2, 'color_mean': 'mediumorchid', 'color_std': 'plum'},
    'PYRDB': {'data': df3, 'color_mean': 'darkorange', 'color_std': 'navajowhite'}
}

# Plot the mean and std histograms for each dataframe
for i, (df_name, properties) in enumerate(dataframes.items()):
    df = properties['data']
    
    # Plot mean histogram
    axes[0, i].hist(df['mean'], bins=30, color=properties['color_mean'], alpha=0.7)
    axes[0, i].set_title(f"Mean Distribution for {df_name}", fontsize=14)
    axes[0, i].set_xlabel("Mean", fontsize=16)
    axes[0, i].set_ylabel("Frequency", fontsize=16)
    
    # Plot std histogram
    axes[1, i].hist(df['std'], bins=30, color=properties['color_std'], alpha=0.7)
    axes[1, i].set_title(f"Standard Deviation Distribution for {df_name}", fontsize=14)
    axes[1, i].set_xlabel("Standard Deviation", fontsize=16)
    axes[1, i].set_ylabel("Frequency", fontsize=16)

# Adjust layout to prevent overlapping labels
plt.tight_layout()
plt.show()



In [37]:
# Create a 2x3 grid for violin plots
fig, axes = plt.subplots(2, 3, figsize=(18, 10), dpi=600)

# Define dataframes, titles, and colors
dataframes = {
    'INDDB': {'data': df1, 'color': 'royalblue'},
    'DIADB': {'data': df2, 'color': 'mediumorchid'},
    'PYRDB': {'data': df3, 'color': 'darkorange'}
}

# Plot the mean and std violin plots for each dataframe in a 2x3 grid
for i, (df_name, properties) in enumerate(dataframes.items()):
    # Plot mean violin plot (first row)
    sns.violinplot(y=properties['data']['mean'], ax=axes[0, i], color=properties['color'])
    #axes[0, i].set_title(f"Mean Distribution for {df_name}", fontsize=18)
    axes[0, i].set_xlabel("Mean", fontsize=20)
    axes[0, i].set_ylabel("Density", fontsize=20)
    axes[0, i].tick_params(axis='x', labelsize=20)  # Explicit x-axis font size

    # Plot standard deviation violin plot (second row)
    sns.violinplot(y=properties['data']['std'], ax=axes[1, i], color=properties['color'])
    #axes[1, i].set_title(f"Standard Deviation Distribution for {df_name}", fontsize=18)
    axes[1, i].set_xlabel("Standard deviation", fontsize=20)
    axes[1, i].set_ylabel("Density", fontsize=20)
    axes[1, i].tick_params(axis='x', labelsize=20)  # Explicit x-axis font size

# Adjust layout to ensure all labels fit well
plt.tight_layout()
plt.show()
